In [1]:
import h5py
import scipy.io
import matplotlib.pyplot as plt
import numpy as np
import pickle
import os

# Preprocess battery data from mat

# Load data
work_folder_path = 'D:\Battery_Problem'
battery_prj_path = os.path.join(
    work_folder_path, 'data-driven-prediction-of-battery-cycle-life-before-capacity-degradation-master')
f = h5py.File(os.path.join(work_folder_path, battery_prj_path, 'Data',
                           'battery_batchdata_combined.mat'))

# Helper


def get_batch_cell_as_string(batch_cell):
    return ''.join(np.char.mod('%c', np.hstack(batch_cell)))


# Extract data
output_cycles = []
output_battery_infos = []


def pop_battery_info(battery_order, policy, policy_readable, barcode, cycle_life, cycle_count):
    output_battery_infos.append({
        'battery_order': battery_order,
        'policy': policy,
        'policy_readable': policy_readable,
        'barcode': barcode,
        'cycle_life': cycle_life,
        'cycle_count': cycle_count,
    })


def print_battery_info_csv(path):
    with open(path, 'w') as f:
        f.write(
            'battery_order,policy,policy_readable,barcode,cycle_life,cycle_count\n')
        for battery_info in output_battery_infos:
            f.write(f"{battery_info['battery_order']},{battery_info['policy']},{battery_info['policy_readable']},{battery_info['barcode']},{battery_info['cycle_life']},{battery_info['cycle_count']}\n")


def pop_cycle(battery_order, cycle_order, c1_avg_T, c2_avg_T, c1a_I_dt, I_max, Qd_max, Qc_max):
    output_cycles.append({
        'battery_order': battery_order,
        'cycle_order': cycle_order,
        'c1_avg_T': c1_avg_T,
        'c2_avg_T': c2_avg_T,
        'c1a_I_dt': c1a_I_dt,
        'I_max': I_max,
        'Qd_max': Qd_max,
        'Qc_max': Qc_max,
        'Qi': (Qd_max + Qc_max) / 2,
        'percent_Qi_1st': 0,
    })


def print_csv(path):
    with open(path, 'w') as f:
        f.write(
            'battery_order,cycle_order,c1_avg_T,c2_avg_T,I_dt,I_max,Qd_max,Qc_max,Qi,percent_Qi_1st\n')
        for cycle in output_cycles:
            f.write(f"{cycle['battery_order']},{cycle['cycle_order']},{cycle['c1_avg_T']},{cycle['c2_avg_T']},{cycle['I_dt']},{cycle['I_max']},{cycle['Qd_max']},{cycle['Qc_max']},{cycle['Qi']},{cycle['percent_Qi_1st']}\n")

In [2]:
batch = f['batch_combined']

In [3]:
list(batch.keys())

['Vdlin',
 'barcode',
 'channel_id',
 'cycle_life',
 'cycles',
 'policy',
 'policy_readable',
 'summary']

In [4]:
def battery_info_iterator():
    battery_count = batch['policy'].shape[0]
    for battery_order in range(battery_count):
        policy = get_batch_cell_as_string(
            f[batch['policy'][battery_order, 0]][()])
        policy_readable = get_batch_cell_as_string(
            f[batch['policy_readable'][battery_order, 0]][()])
        # barcode = np.hstack(f[batch['barcode'][battery_order, 0]][()])
        barcode = ''
        cycle_life = np.hstack(f[batch['cycle_life'][battery_order, 0]][()])[0]
        cycle_count = f[batch['cycles'][battery_order, 0]]['I'].shape[0] - 1

        # barcode = np.hstack(
        #     list(map(lambda x:
        #              [int(x) >> 24, (x >> 16) & (int(2**8) - 1), (x >> 8)
        #               & (int(2**8) - 1), x & (int(2**8) - 1)],
        #              barcode)))

        # barcode = get_batch_cell_as_string(barcode)

        yield battery_order + 1, policy, policy_readable, barcode, cycle_life, cycle_count


# for battery_order, policy, policy_readable, barcode, cycle_life, cycle_count in battery_info_iterator():
#     print(
#         f'Battery {battery_order} - {policy_readable} - {barcode} - {cycle_life} - {cycle_count}')

In [5]:
for battery_order, policy, policy_readable, barcode, cycle_life, cycle_count in battery_info_iterator():
    pop_battery_info(battery_order, policy, policy_readable,
                     barcode, cycle_life, cycle_count)

In [6]:
def cycle_iterator(battery_order):
    # cl = f[batch['cycle_life'][0, 0]][()]
    cycles = f[batch['cycles'][battery_order - 1, 0]]

    for j in range(cycles['I'].shape[0]):
        I = np.hstack((f[cycles['I'][j, 0]][()]))
        Qc = np.hstack((f[cycles['Qc'][j, 0]][()]))
        Qd = np.hstack((f[cycles['Qd'][j, 0]][()]))
        Qdlin = np.hstack((f[cycles['Qdlin'][j, 0]][()]))
        T = np.hstack((f[cycles['T'][j, 0]][()]))
        Tdlin = np.hstack((f[cycles['Tdlin'][j, 0]][()]))
        V = np.hstack((f[cycles['V'][j, 0]][()]))

        dQdV = np.hstack((f[cycles['discharge_dQdV'][j, 0]][()]))
        t = np.hstack((f[cycles['t'][j, 0]][()]))

        yield I, Qc, Qd, Qdlin, T, Tdlin, V, dQdV, t

In [7]:
battery_cycles_ouptput = []


for battery in output_battery_infos:
    output_cycles = []
    battery_order = battery['battery_order']
    current_cycle = 0
    real_cycle = 0

    for _cycle in cycle_iterator(battery_order):
        I, Qc, Qd, Qdlin, T, Tdlin, V, dQdV, t = _cycle
        real_cycle = real_cycle + 1
        print(f'Battery {battery_order} - Cycle {real_cycle}')
        if (len(I) < 10):
            continue
        Qc_max = np.max(Qc)

        if Qc_max < 0.88:
            break
            # continue

        current_cycle = current_cycle + 1
        cycle_order = current_cycle

        Qd_max = np.max(Qd)

        end_c1_time = 0
        for i in range(len(T)):
            if Qc[i] >= Qc_max:
                if i == 0 or i - 1 == end_c1_time:
                    end_c1_time = i
                    continue
                end_c1_time = i
                break
        print(str(end_c1_time) + "/" + str(len(T)))

        I_max = np.max(I[0:end_c1_time])
        c1_avg_T = np.mean(T[0:end_c1_time])
        c2_avg_T = np.mean(T[end_c1_time:])

        # TODO: Trong pha 1, khi gía trị hiệu điện thế từ 3.1V đến 3.3V, tính tổng I*Δt:

        index = 0
        t_I_dt = []
        I_I_dt = []

        while index < end_c1_time and V[index] <= 3.1:
            index = index + 1

        while index < end_c1_time and V[index] < 3.3:
            t_I_dt.append(t[index])
            I_I_dt.append(I[index])
            index = index + 1

        c1a_I_dt = np.trapz(I_I_dt, t_I_dt)

        # TODO: Xem xét liệu đến chu trình này thì Qi < 0.8*Qi lần sạc 1 đầu tiên? Nếu có thì pin hư.

        pop_cycle(battery_order, cycle_order, c1_avg_T,
                  c2_avg_T, c1a_I_dt, I_max, Qd_max, Qc_max)

    Qi_1st = output_cycles[0]['Qi']
    for cycle in output_cycles:
        cycle['percent_Qi_1st'] = cycle['Qi'] / Qi_1st

    battery['cycle_count'] = len(output_cycles)
    battery_cycles_ouptput = battery_cycles_ouptput + output_cycles

output_cycles = battery_cycles_ouptput

Battery 1 - Cycle 1
Battery 1 - Cycle 2
656/1087
Battery 1 - Cycle 3
669/1117
Battery 1 - Cycle 4
650/1114
Battery 1 - Cycle 5
680/1138
Battery 1 - Cycle 6
657/1102
Battery 1 - Cycle 7
671/1106
Battery 1 - Cycle 8
657/1097
Battery 1 - Cycle 9
683/1131
Battery 1 - Cycle 10
688/1130
Battery 1 - Cycle 11
681/1133
Battery 1 - Cycle 12
2304/2730
Battery 1 - Cycle 13
686/1145
Battery 1 - Cycle 14
667/1115
Battery 1 - Cycle 15
667/1108
Battery 1 - Cycle 16
670/1125
Battery 1 - Cycle 17
663/1105
Battery 1 - Cycle 18
651/1094
Battery 1 - Cycle 19
662/1101
Battery 1 - Cycle 20
676/1125
Battery 1 - Cycle 21
685/1122
Battery 1 - Cycle 22
686/1128
Battery 1 - Cycle 23
675/1122
Battery 1 - Cycle 24
690/1132
Battery 1 - Cycle 25
656/1110
Battery 1 - Cycle 26
674/1127
Battery 1 - Cycle 27
676/1134
Battery 1 - Cycle 28
666/1116
Battery 1 - Cycle 29
666/1111
Battery 1 - Cycle 30
651/1097
Battery 1 - Cycle 31
669/1123
Battery 1 - Cycle 32
673/1109
Battery 1 - Cycle 33
694/1136
Battery 1 - Cycle 34
660/11

In [8]:
print_battery_info_csv(os.path.join(work_folder_path, 'battery_infos.csv'))

In [9]:
# output_cycles
print_csv(os.path.join(work_folder_path, 'battery_cycles.csv'))